In [4]:
from six.moves import cPickle as pickle #for performance

def load_dict(filename_):
    with open(filename_, 'rb') as f:
        ret_di = pickle.load(f)
    return ret_di

In [20]:
dict_frames = load_dict('./data.pkl')

In [21]:
[print('label' +v + 'value' +i) for i, v in zip(["Calculations", "Income Statement", "Cash Flow Statement","Balance Sheet"],["calculations", "income_statement", "cash_flow_statement","balance_sheet"])]                

labelcalculationsvalueCalculations
labelincome_statementvalueIncome Statement
labelcash_flow_statementvalueCash Flow Statement
labelbalance_sheetvalueBalance Sheet


[None, None, None, None]

In [ ]:
for k in list(name_dict):
    v = name_dict.pop(k)
    ...
    name_dict[new_key] = v

In [22]:
dict_frames.keys()

dict_keys([('CMG', 'FY', 'calculations', 'Original'), ('CMG', 'FY', 'calculations', 'Normalised'), ('CMG', 'FY', 'calculations', 'Pos Correlated Pairs'), ('CMG', 'FY', 'calculations', 'Neg Correlated Pairs'), ('CMG', 'FY', 'calculations', 'Principal Component'), ('CMG', 'FY', 'calculations', 'Benchmark'), ('CMG', 'FY', 'calculations', 'Better Than Bench'), ('CMG', 'FY', 'calculations', 'Worse Than Bench'), ('CMG', 'FY', 'calculations', 'Volatile'), ('CMG', 'FY', 'calculations', 'Stable'), ('CMG', 'FY', 'calculations', 'Smooth'), ('CMG', 'FY', 'calculations', 'Price Pos Correlated'), ('CMG', 'FY', 'calculations', 'Price Neg Correlated'), ('CMG', 'FY', 'income_statement', 'Original'), ('CMG', 'FY', 'income_statement', 'Normalised'), ('CMG', 'FY', 'income_statement', 'Pos Correlated Pairs'), ('CMG', 'FY', 'income_statement', 'Neg Correlated Pairs'), ('CMG', 'FY', 'income_statement', 'Principal Component'), ('CMG', 'FY', 'income_statement', 'Benchmark'), ('CMG', 'FY', 'income_statement', '

In [7]:
dict_frames["BJ's", 'QTR', 'Calculations', 'Normalised']

TypeError: unhashable type: 'list'

In [1]:
import pandas as pd
pd.set_option('display.max_columns', None)
import dash
from dash import Dash
from dash.dependencies import Input, Output
import dash_core_components as dcc
import dash_html_components as html
import colorlover as cl
import numpy as np
from flask import Flask

pd.set_option('display.max_columns', None)

import intrinio

from sklearn.preprocessing import MinMaxScaler
from sklearn.preprocessing import StandardScaler

def Standardisation(df):
    listed = list(df)
    scaler = StandardScaler()
    scaled = scaler.fit_transform(df)
    df = pd.DataFrame(scaled)
    df.columns = listed
    return df

def Normalisation(df):
    listed = list(df)
    index = df.index
    scaler = MinMaxScaler()
    scaled = scaler.fit_transform(df)
    df = pd.DataFrame(scaled)
    df.columns = listed
    df.index = index
    return df



import intrinio
intrinio.client.username = 'cae7d0c54c6e7fd5363fc315b7fc7a4a'
intrinio.client.password = '8dc75b7fcc16e0a4782b789785eb0241'

#for period in ["FY","QTR","TTM","YTD"]: For now I will just leave them out
#statement = ["calculations", "income_statement","balance_sheet","cash_flow_statement"]

def price_extract(ticker, period):
    periods = ""
    if period == "QTR":
        periods = "quarterly"
        print("yae")
    elif period =="FY":
        periods = "yearly"
        print("no")

        
    price = intrinio.prices( ticker,start_date=2008, frequency = periods, sort_order='asc')
    
    price.index = pd.to_datetime(price.index, format="%Y-%m-%d")
    price["year"] = pd.DatetimeIndex(price.index).year
    
    price  = price[price.index>"2008-12-31"] 
    
    if period == "QTR":
        price['quarter'] = pd.PeriodIndex(price.index, freq='Q-MAR').strftime('Q%q')
        price["year"] = price["year"].map(str) + price["quarter"]
                         # Assumes that quarter is march.
        price_norm = pd.concat((Normalisation(price.drop(["year","quarter"],axis=1)),price[["year","quarter"]]),axis=1)
    else:
        price_norm = pd.concat((Normalisation(price.drop("year",axis=1)),price["year"]),axis=1)
    

    return price, price_norm
    

def data_extract(ticker, period, request):
    
    
    DARS_2 = intrinio.financials(ticker, type=period, statement=request)

    DARS_1 = DARS_2.fillna(value=0.01)
    DARS_1 = DARS_1.replace(0, 0.01)

    DARS_N = DARS_1

    DARS_N  = DARS_N[DARS_N.index.get_level_values(0)>2008]

    DARS_N = Normalisation(DARS_N)
    DARS_N = DARS_N.replace(0, 0.01)
    DARS_1  = DARS_1[DARS_1.index.get_level_values(0)>2008]

    DARS_N.reset_index(inplace=True)
    
    DARS_1.reset_index(inplace=True)

    if period in ["QTR"]:

        DARS_N["year"] = DARS_N["year"].map(str)  + DARS_N["period"]

        DARS_N.drop("period",axis=1, inplace=True)

        DARS_1.reset_index(inplace=True)

        DARS_1["year"] = DARS_1["year"].map(str)  + DARS_1["period"]
        DARS_1.drop("period",axis=1, inplace=True)


    org, nor = price_extract(ticker, period)

    DARS_N = pd.merge(DARS_N, nor[["adj_close","year"]], on="year", how="left")
    DARS_1 = pd.merge(DARS_1, org[["adj_close","year"]], on="year", how="left")


    return DARS_1, DARS_N

ticks = ["BJRI","CMG"]
for ticker in ticks: 
    for period in ["FY","QTR"]:
        if period == "FY":
            for request in ["calculations", "income_statement", "balance_sheet", "cash_flow_statement"]:
                 #for request in ["calculations"]:
                original, normalised = data_extract(ticker, period, request)
                original.to_csv("org_"+period+"_"+request+"_"+ticker+".csv", index=False)
                normalised.to_csv("sta_"+period+"_"+request+"_"+ticker+".csv", index=False)
        elif period == "QTR":
            for request in ["calculations"]:
                 #for request in ["calculations"]:
                original, normalised = data_extract(ticker, period, request)
                original.to_csv("org_"+period+"_"+request+"_"+ticker+".csv", index=False)
                normalised.to_csv("sta_"+period+"_"+request+"_"+ticker+".csv", index=False)

In [44]:
def correlation(boola, vals,select, normalised):
    if boola:
        norms = normalised.corr()["adj_close"].sort_values()[:10].index.values; norms
    else:
        norms = normalised.corr()["adj_close"].sort_values()[-10:].index.values; norms
        
    dis  = {}
    for i in norms:
        das = normalised[norms].corr()[i]
        dis[i] = das.sum() 
        
    corr = pd.DataFrame(list(dis.values()), index=list(dis.keys())).sort_values(0).ix[:3].index.values

    return corr
    
#     related = pd.DataFrame(list(dis.values()), index=list(dis.keys())).sort_values(0).ix[:select].index.values
#     related = normalised[related]
#     return related

In [94]:
np.set_printoptions(threshold=np.nan)

In [148]:
def pca_transform(normalised,code):
    if code == "calculations":
        calc_pca = pd.read_csv("calc_pca.csv") # calc_pca wass created by hand labelling
    elif code == "balance_sheet":
        calc_pca = pd.read_csv("ass_pca.csv") 
    elif code == "income_statement":
        calc_pca = pd.read_csv("inc_pca.csv") # calc_pca wass created by hand labelling
    elif code == "cash_flow_statement":
        calc_pca = pd.read_csv("cfs_pca.csv")   
    
    calc_pca = calc_pca.dropna().reset_index(drop=True)
    print(calc_pca.columns)
    print(calc_pca.values)
    print(normalised.columns)
    
    fair_values = list(set(calc_pca["Type"].unique()).intersection(normalised.columns))
    
    normalised = normalised[fair_values]
    
    calc_pca = calc_pca[calc_pca["Type"].isin(fair_values)].reset_index()
    
    print(calc_pca["Dimension"].unique())
    pca_df = pd.DataFrame()
    for i in calc_pca["Dimension"].unique():
        normalised_profit = normalised[calc_pca[calc_pca["Dimension"]==i]["Type"].values]

        import numpy as np
        from sklearn.decomposition import PCA

        pca = PCA(n_components=1)
        pca.fit(normalised_profit)
        X = pca.transform(normalised_profit) 
        X = list(X.reshape(-1))
        pca_df[i]= list(X)

    
    

    return pca_df

In [123]:
def corrsa(boola,select,diff_frame):
    if boola:

        norms = diff_frame.sum().sort_values(ascending=False)[:10].index.values
    else:
        norms = diff_frame.sum().sort_values(ascending=False)[-10:].index.values

    dis  = {}
    for i in norms:
        das = diff_frame[norms].corr()[i]
        dis[i] = das.sum()

    related = pd.DataFrame(list(dis.values()), index=list(dis.keys()))
    print(related)
    related = related.sort_values(0)[:select].index.values
    return related

In [141]:
# Bench comp here has a null df, and it has to be wixed
def bench_comp(bj_qtr,cmg_qtr,code,period):
    if period == "QTR":
        dwad = {"calculations":20, "income_statement":16, "cash_flow_statement":16,"balance_sheet":12}
    elif period == "FY":
        dwad = {"calculations":5, "income_statement":4, "cash_flow_statement":4,"balance_sheet":3}


    rwad = dwad[code]
    
    name = np.where(bj_qtr.ix[:,1:].sum().values > rwad, bj_qtr.ix[:,1:].sum().index, np.nan)

    framed = pd.DataFrame(name)

    framed = framed.dropna().reset_index(drop=True)

    name = np.where(cmg_qtr.ix[:,1:].sum().values > rwad, cmg_qtr.ix[:,1:].sum().index, np.nan)

    framed_comp = pd.DataFrame(name)

    framed_comp = framed_comp.dropna().reset_index(drop=True)

    full = list(set(framed_comp[0]).intersection(framed[0]))

    diff_frame = pd.DataFrame()
    for i in full:
        diff_frame[i] = bj_qtr[i] - cmg_qtr[i]

    positive = corrsa(True,3,diff_frame)
    negative = corrsa(False,3,diff_frame)
    return positive, negative, full

In [59]:
cmg_qtr

year  revenuegrowth     nopat  nopatmargin  investedcapital  \
0  2009       0.010000  0.010000     0.269629         0.010000   
1  2010       0.979117  0.275001     0.755233         0.583874   
2  2011       1.000000  0.522786     0.971995         0.698048   
3  2012       0.658933  0.505243     0.687060         0.826994   
4  2013       0.424958  0.193562     0.010000         0.921312   
5  2014       0.407689  0.400594     0.236990         0.939696   
6  2015       0.390889  1.000000     1.000000         0.955623   
7  2016       0.352222  0.998298     0.844585         1.000000   

   investedcapitalturnover  investedcapitalincreasedecrease  freecashflow  \
0                 0.010000                         0.010000      0.351662   
1                 0.866065                         0.010000      0.351662   
2                 0.953720                         0.885437      0.105894   
3                 0.914323                         1.000000      0.010000   
4                 0.872592                         0.731452      0.062457   
5                 0.894348                         0.142569      0.668308   
6                 0.955302                         0.123517      1.000000   
7                 1.000000                         0.344155      0.812953   

   netnonopex  netnonopobligations      ebit  depreciationandamortization  \
0    1.000000             0.302041  0.010000                     0.010000   
1    0.396343             0.010000  0.248252                     0.118513   
2    0.192182             0.005919  0.531307                     0.247933   
3    0.010000             0.073971  0.500825                     0.429027   
4    0.166795             0.119324  0.111475                     0.619783   
5    0.305571             0.454279  0.382891                     0.778663   
6    0.959117             0.669280  1.000000                     0.879022   
7    0.822652             1.000000  0.993007                     1.000000   

     ebitda     capex   dfcfnwc     dfnwc       nwc      debt  \
0  0.010000  0.010000  1.000000  0.782402  0.782402  0.010000   
1  0.186306  0.194913  0.615056  1.000000  1.000000  0.010000   
2  0.395966  0.634432  0.637236  0.932219  0.932219  0.010000   
3  0.467863  0.922900  0.548742  0.699278  0.699278  0.010000   
4  0.358111  1.000000  0.417549  0.533663  0.533663  0.010000   
5  0.575999  0.304051  0.371832  0.482240  0.482240  0.391892   
6  0.945028  0.458677  0.348383  0.503444  0.503444  0.679054   
7  1.000000  0.910914  0.010000  0.010000  0.010000  1.000000   

   ltdebtandcapleases   netdebt  totalcapital  bookvaluepershare  \
0            0.010000  0.302041      0.010000           0.010000   
1            0.010000  0.010000      0.680605           0.735336   
2            0.010000  0.005919      0.786123           0.820974   
3            0.010000  0.073971      0.879254           0.927429   
4            0.010000  0.119324      0.949252           1.000000   
5            0.391892  0.454279      0.961674           0.886285   
6            0.679054  0.669280      0.986016           0.868349   
7            1.000000  1.000000      1.000000           0.816393   

   tangbookvaluepershare  marketcap  enterprisevalue  pricetobook  \
0               0.010000   0.010000         0.010000     0.010000   
1               0.731911   0.556890         0.664699     0.866469   
2               0.818966   0.845672         0.847356     0.944781   
3               0.926559   0.480686         0.625836     0.624169   
4               1.000000   0.423914         0.595678     0.546224   
5               0.884704   1.000000         1.000000     1.000000   
6               0.865602   0.726979         0.854581     0.908410   
7               0.811963   0.454775         0.723981     0.823963   

   pricetotangiblebook  pricetorevenue  pricetoearnings  dividendyield  \
0             0.010000        0.231508         0.593131           0.01   
1             0.868989        0.926563         0.74

In [60]:
bj_qtr

year  revenuegrowth     nopat  nopatmargin  investedcapital  \
0  2009       0.663842  0.235020     0.760776         0.010000   
1  2010       0.832188  0.349584     0.894735         0.064284   
2  2011       0.898157  0.432136     0.873943         0.060687   
3  2012       0.818352  0.568251     0.936699         0.348273   
4  2013       0.753949  0.677880     0.938111         0.498691   
5  2014       1.000000  0.936768     1.000000         0.761603   
6  2015       0.555879  1.000000     0.970001         0.957985   
7  2016       0.010000  0.010000     0.010000         1.000000   

   investedcapitalturnover  investedcapitalincreasedecrease  freecashflow  \
0                 0.010000                         0.012355      0.010000   
1                 0.256253                         0.233124      0.388678   
2                 0.607836                         0.010000      0.559146   
3                 0.741492                         1.000000      0.397921   
4                 0.737664                         0.528929      0.675893   
5                 1.000000                         0.915262      0.853481   
6                 0.904756                         0.686783      1.000000   
7                 0.463544                         0.156645      0.006639   

   netnonopex  netnonopobligations      ebit  depreciationandamortization  \
0    0.807105             1.000000  0.226343                     0.010000   
1    0.707535             0.921267  0.342378                     0.089502   
2    1.000000             0.690212  0.425324                     0.160240   
3    0.629470             0.612266  0.573013                     0.268305   
4    0.636904             0.387679  0.678037                     0.408488   
5    0.384602             0.031459  0.924002                     0.578016   
6    0.010000             0.010000  1.000000                     0.811897   
7    0.319642             0.731250  0.010000                     1.000000   

     ebitda     capex   dfcfnwc     dfnwc       nwc  debt  ltdebtandcapleases  \
0  0.112464  0.027351  0.929285  0.010000  0.010000  0.01                0.01   
1  0.241740  0.010000  1.000000  0.209955  0.209955  0.01                0.01   
2  0.334955  0.260474  0.583805  0.354691  0.354691  0.01                0.01   
3  0.498803  0.575594  0.578430  0.392961  0.392961  0.01                0.01   
4  0.622851  0.595432  0.596578  0.649410  0.649410  0.01                0.01   
5  0.894483  0.957068  0.297015  1.000000  1.000000  0.01                0.01   
6  1.000000  0.990222  0.439358  0.811001  0.811001  0.01                0.01   
7  0.010000  1.000000  0.010000  0.108196  0.108196  0.01                0.01   

    netdebt  totalcapital  bookvaluepershare  tangbookvaluepershare  \
0  1.000000      0.010000           0.010000               0.010000   
1  0.921267      0.075403           0.079688               0.079538   
2  0.690212      0.239215           0.239842               0.239758   
3  0.612266      0.380807           0.378665               0.378624   
4  0.387679      0.586044           0.597164               0.596944   
5  0.031459      0.918846           0.918798               0.918784   
6  0.010000      1.000000           1.000000               1.000000   
7  0.731250      0.490716           0.551924               0.550909   

   marketcap  enterprisevalue  pricetobook  pricetotangiblebook  \
0   0.010000         0.010000     0.010000             0.010000   
1   0.209104         0.216192     0.631288             0.643693   
2   0.421639         0.427283     0.918235             0.927890   
3   0.353469         0.350870     0.523418             0.522287   
4   0.738295         0.744178     1.000000             1.000000   
5   1.000000         1.000000     0.983072             0.977509   
6   0.655399         0.634489     0.452019             0.442105   
7   0.448379         0.457856     0.585244             0.582595   

   pricetorevenue  pricetoearnings  dividendyi

In [64]:
full

[]

In [66]:
framed_comp

0
0             investedcapital
1     investedcapitalturnover
2                totalcapital
3           bookvaluepershare
4       tangbookvaluepershare
5             enterprisevalue
6                 pricetobook
7         pricetotangiblebook
8         evtoinvestedcapital
9                 evtorevenue
10                 evtoebitda
11                    evtoocf
12                 ebitmargin
13          interestburdenpct
14                 efftaxrate
15              assetturnover
16                 arturnover
17                invturnover
18                 faturnover
19                 apturnover
20                        dso
21                        dio
22                        dpo
23              leverageratio
24     compoundleveragefactor
25                       roic
26             roicnnepspread
27                       oroa
28                        roa
29                commontocap
30               altmanzscore
31  ebitlesscapextointerestex
32      nopatlesscapextointex

In [71]:
positive

array(['evtoocf', 'assetturnover', 'roicnnepspread'], dtype=object)

In [135]:
cmg_qtr.ix[:,1:].sum()

accountspayable                          4.238240
accountsreceivable                       2.937364
accruedexpenses                          3.023444
cashandequivalents                       3.825054
commitmentsandcontingencies              0.070000
commonequity                             4.205520
currentdeferredtaxassets                 4.454700
goodwill                                 0.070000
longtermdebt                             2.110946
longterminvestments                      2.366348
netinventory                             3.650580
netppe                                   4.012507
noncurrentdeferredrevenue                3.514154
noncurrentdeferredtaxliabilities         3.315130
noncurrentnotereceivables                2.053699
othernoncurrentassets                    3.092854
othernoncurrentliabilities               4.091238
prepaidexpenses                          4.140052
retainedearnings                         3.623158
shortterminvestments                     3.115547


In [138]:
dwad

5

In [139]:
ticks = ["CMG","BJRI"]
dwad = {"calculations":5, "income_statement":4, "cash_flow_statement":4,"balance_sheet":3}

for ticker in ticks: 
    for period in ["FY","QTR"]:
        if period == "FY":
            for request in ["calculations", "income_statement", "cash_flow_statement","balance_sheet"]:
                rwad = dwad[request]
                original = pd.read_csv("org_"+period+"_"+request+"_"+ticker+".csv")
                normalised = pd.read_csv("sta_"+period+"_"+request+"_"+ticker+".csv")
            
                for i in ticks:
                    if i not in ticker:
                        bench = pd.read_csv("sta_"+period+"_"+request+"_"+i+".csv")
                        bj_qtr = normalised
                        cmg_qtr = bench
                        name = np.where(bj_qtr.ix[:,1:].sum().values > rwad, bj_qtr.ix[:,1:].sum().index, np.nan)

                        framed = pd.DataFrame(name)

                        framed = framed.dropna().reset_index(drop=True)

                        name = np.where(cmg_qtr.ix[:,1:].sum().values > rwad, cmg_qtr.ix[:,1:].sum().index, np.nan)

                        framed_comp = pd.DataFrame(name)

                        framed_comp = framed_comp.dropna().reset_index(drop=True)

                        full = list(set(framed_comp[0]).intersection(framed[0]))

                        diff_frame = pd.DataFrame()
                        for i in full:
                            diff_frame[i] = bj_qtr[i] - cmg_qtr[i]

                        positive = normalised[corrsa(True,3,diff_frame)]
                        negative = normalised[corrsa(False,3,diff_frame)]
                        
                        
                        positive.to_csv("sta_"+period+"_"+request+"_"+ticker+"pos_benched_to_"+i+".csv")
                        negative.to_csv("sta_"+period+"_"+request+"_"+ticker+"pos_benched_to_"+i+".csv")
                        



                            0
ebitmargin           6.533125
oroa                 6.230008
roa                  6.157111
evtoocf             -0.071758
roic                 6.324171
pricetobook          5.320250
pricetotangiblebook  5.301342
roicnnepspread       5.056634
assetturnover        4.927484
                            0
ebitmargin           6.533125
oroa                 6.230008
roa                  6.157111
evtoocf             -0.071758
roic                 6.324171
pricetobook          5.320250
pricetotangiblebook  5.301342
roicnnepspread       5.056634
assetturnover        4.927484
                                   0
weightedavedilutedsharesos  3.749716
netincometocommon           4.703481
netincome                   4.703481
netincomecontinuing         4.703481
otherspecialcharges         4.045697
weightedavebasicsharesos    2.807106
operatingcostofrevenue      6.428365
totalcostofrevenue          6.428365
operatingrevenue            7.038320
totalrevenue                7.

In [79]:
def volat(boola,select,frame,vola):
    if boola:
        
        norms = vola.std().sort_values(ascending=False).ix[:10].index.values
    else:
        norms = vola.std().sort_values(ascending=False).ix[-10:].index.values

    dis  = {}
    for i in norms:
        das = frame[norms].corr()[i]
        dis[i] = das.sum() 

    related = pd.DataFrame(list(dis.values()), index=list(dis.keys())).sort_values(0).ix[:select].index.values
    return related


In [8]:
def smoothed(bj_qtr):
    
    smooth = pd.rolling_mean(bj_qtr.ix[:,1:], window=8)

    smooth_rev = pd.rolling_mean(bj_qtr.iloc[::-1].ix[:,1:].reset_index(drop=True), window=8)

    smooth_rev.head()

    smooth.ix[:6] = smooth_rev[-7:][::-1].reset_index(drop=True)
    return smooth

In [155]:
normalised

year  revenuegrowth     nopat  nopatmargin  investedcapital  \
0  2009       0.010000  0.010000     0.269629         0.010000   
1  2010       0.979117  0.275001     0.755233         0.583874   
2  2011       1.000000  0.522786     0.971995         0.698048   
3  2012       0.658933  0.505243     0.687060         0.826994   
4  2013       0.424958  0.193562     0.010000         0.921312   
5  2014       0.407689  0.400594     0.236990         0.939696   
6  2015       0.390889  1.000000     1.000000         0.955623   
7  2016       0.352222  0.998298     0.844585         1.000000   

   investedcapitalturnover  investedcapitalincreasedecrease  freecashflow  \
0                 0.010000                         0.010000      0.351662   
1                 0.866065                         0.010000      0.351662   
2                 0.953720                         0.885437      0.105894   
3                 0.914323                         1.000000      0.010000   
4                 0.872592                         0.731452      0.062457   
5                 0.894348                         0.142569      0.668308   
6                 0.955302                         0.123517      1.000000   
7                 1.000000                         0.344155      0.812953   

   netnonopex  netnonopobligations      ebit  depreciationandamortization  \
0    1.000000             0.302041  0.010000                     0.010000   
1    0.396343             0.010000  0.248252                     0.118513   
2    0.192182             0.005919  0.531307                     0.247933   
3    0.010000             0.073971  0.500825                     0.429027   
4    0.166795             0.119324  0.111475                     0.619783   
5    0.305571             0.454279  0.382891                     0.778663   
6    0.959117             0.669280  1.000000                     0.879022   
7    0.822652             1.000000  0.993007                     1.000000   

     ebitda     capex   dfcfnwc     dfnwc       nwc      debt  \
0  0.010000  0.010000  1.000000  0.782402  0.782402  0.010000   
1  0.186306  0.194913  0.615056  1.000000  1.000000  0.010000   
2  0.395966  0.634432  0.637236  0.932219  0.932219  0.010000   
3  0.467863  0.922900  0.548742  0.699278  0.699278  0.010000   
4  0.358111  1.000000  0.417549  0.533663  0.533663  0.010000   
5  0.575999  0.304051  0.371832  0.482240  0.482240  0.391892   
6  0.945028  0.458677  0.348383  0.503444  0.503444  0.679054   
7  1.000000  0.910914  0.010000  0.010000  0.010000  1.000000   

   ltdebtandcapleases   netdebt  totalcapital  bookvaluepershare  \
0            0.010000  0.302041      0.010000           0.010000   
1            0.010000  0.010000      0.680605           0.735336   
2            0.010000  0.005919      0.786123           0.820974   
3            0.010000  0.073971      0.879254           0.927429   
4            0.010000  0.119324      0.949252           1.000000   
5            0.391892  0.454279      0.961674           0.886285   
6            0.679054  0.669280      0.986016           0.868349   
7            1.000000  1.000000      1.000000           0.816393   

   tangbookvaluepershare  marketcap  enterprisevalue  pricetobook  \
0               0.010000   0.010000         0.010000     0.010000   
1               0.731911   0.556890         0.664699     0.866469   
2               0.818966   0.845672         0.847356     0.944781   
3               0.926559   0.480686         0.625836     0.624169   
4               1.000000   0.423914         0.595678     0.546224   
5               0.884704   1.000000         1.000000     1.000000   
6               0.865602   0.726979         0.854581     0.908410   
7               0.811963   0.454775         0.723981     0.823963   

   pricetotangiblebook  pricetorevenue  pricetoearnings  dividendyield  \
0             0.010000        0.231508         0.593131           0.01   
1             0.868989        0.926563         0.74

In [160]:
normalised

year  revenuegrowth     nopat  nopatmargin  investedcapital  \
0  2009       0.010000  0.010000     0.269629         0.010000   
1  2010       0.979117  0.275001     0.755233         0.583874   
2  2011       1.000000  0.522786     0.971995         0.698048   
3  2012       0.658933  0.505243     0.687060         0.826994   
4  2013       0.424958  0.193562     0.010000         0.921312   
5  2014       0.407689  0.400594     0.236990         0.939696   
6  2015       0.390889  1.000000     1.000000         0.955623   
7  2016       0.352222  0.998298     0.844585         1.000000   

   investedcapitalturnover  investedcapitalincreasedecrease  freecashflow  \
0                 0.010000                         0.010000      0.351662   
1                 0.866065                         0.010000      0.351662   
2                 0.953720                         0.885437      0.105894   
3                 0.914323                         1.000000      0.010000   
4                 0.872592                         0.731452      0.062457   
5                 0.894348                         0.142569      0.668308   
6                 0.955302                         0.123517      1.000000   
7                 1.000000                         0.344155      0.812953   

   netnonopex  netnonopobligations      ebit  depreciationandamortization  \
0    1.000000             0.302041  0.010000                     0.010000   
1    0.396343             0.010000  0.248252                     0.118513   
2    0.192182             0.005919  0.531307                     0.247933   
3    0.010000             0.073971  0.500825                     0.429027   
4    0.166795             0.119324  0.111475                     0.619783   
5    0.305571             0.454279  0.382891                     0.778663   
6    0.959117             0.669280  1.000000                     0.879022   
7    0.822652             1.000000  0.993007                     1.000000   

     ebitda     capex   dfcfnwc     dfnwc       nwc      debt  \
0  0.010000  0.010000  1.000000  0.782402  0.782402  0.010000   
1  0.186306  0.194913  0.615056  1.000000  1.000000  0.010000   
2  0.395966  0.634432  0.637236  0.932219  0.932219  0.010000   
3  0.467863  0.922900  0.548742  0.699278  0.699278  0.010000   
4  0.358111  1.000000  0.417549  0.533663  0.533663  0.010000   
5  0.575999  0.304051  0.371832  0.482240  0.482240  0.391892   
6  0.945028  0.458677  0.348383  0.503444  0.503444  0.679054   
7  1.000000  0.910914  0.010000  0.010000  0.010000  1.000000   

   ltdebtandcapleases   netdebt  totalcapital  bookvaluepershare  \
0            0.010000  0.302041      0.010000           0.010000   
1            0.010000  0.010000      0.680605           0.735336   
2            0.010000  0.005919      0.786123           0.820974   
3            0.010000  0.073971      0.879254           0.927429   
4            0.010000  0.119324      0.949252           1.000000   
5            0.391892  0.454279      0.961674           0.886285   
6            0.679054  0.669280      0.986016           0.868349   
7            1.000000  1.000000      1.000000           0.816393   

   tangbookvaluepershare  marketcap  enterprisevalue  pricetobook  \
0               0.010000   0.010000         0.010000     0.010000   
1               0.731911   0.556890         0.664699     0.866469   
2               0.818966   0.845672         0.847356     0.944781   
3               0.926559   0.480686         0.625836     0.624169   
4               1.000000   0.423914         0.595678     0.546224   
5               0.884704   1.000000         1.000000     1.000000   
6               0.865602   0.726979         0.854581     0.908410   
7               0.811963   0.454775         0.723981     0.823963   

   pricetotangiblebook  pricetorevenue  pricetoearnings  dividendyield  \
0             0.010000        0.231508         0.593131           0.01   
1             0.868989        0.926563         0.74

In [130]:
period

'FY'

In [127]:
request

'balance_sheet'

In [92]:
normalisedt

year  revenuegrowth     nopat  nopatmargin  investedcapital  \
0  2009       0.663842  0.235020     0.760776         0.010000   
1  2010       0.832188  0.349584     0.894735         0.064284   
2  2011       0.898157  0.432136     0.873943         0.060687   
3  2012       0.818352  0.568251     0.936699         0.348273   
4  2013       0.753949  0.677880     0.938111         0.498691   
5  2014       1.000000  0.936768     1.000000         0.761603   
6  2015       0.555879  1.000000     0.970001         0.957985   
7  2016       0.010000  0.010000     0.010000         1.000000   

   investedcapitalturnover  investedcapitalincreasedecrease  freecashflow  \
0                 0.010000                         0.012355      0.010000   
1                 0.256253                         0.233124      0.388678   
2                 0.607836                         0.010000      0.559146   
3                 0.741492                         1.000000      0.397921   
4                 0.737664                         0.528929      0.675893   
5                 1.000000                         0.915262      0.853481   
6                 0.904756                         0.686783      1.000000   
7                 0.463544                         0.156645      0.006639   

   netnonopex  netnonopobligations      ebit  depreciationandamortization  \
0    0.807105             1.000000  0.226343                     0.010000   
1    0.707535             0.921267  0.342378                     0.089502   
2    1.000000             0.690212  0.425324                     0.160240   
3    0.629470             0.612266  0.573013                     0.268305   
4    0.636904             0.387679  0.678037                     0.408488   
5    0.384602             0.031459  0.924002                     0.578016   
6    0.010000             0.010000  1.000000                     0.811897   
7    0.319642             0.731250  0.010000                     1.000000   

     ebitda     capex   dfcfnwc     dfnwc       nwc  debt  ltdebtandcapleases  \
0  0.112464  0.027351  0.929285  0.010000  0.010000  0.01                0.01   
1  0.241740  0.010000  1.000000  0.209955  0.209955  0.01                0.01   
2  0.334955  0.260474  0.583805  0.354691  0.354691  0.01                0.01   
3  0.498803  0.575594  0.578430  0.392961  0.392961  0.01                0.01   
4  0.622851  0.595432  0.596578  0.649410  0.649410  0.01                0.01   
5  0.894483  0.957068  0.297015  1.000000  1.000000  0.01                0.01   
6  1.000000  0.990222  0.439358  0.811001  0.811001  0.01                0.01   
7  0.010000  1.000000  0.010000  0.108196  0.108196  0.01                0.01   

    netdebt  totalcapital  bookvaluepershare  tangbookvaluepershare  \
0  1.000000      0.010000           0.010000               0.010000   
1  0.921267      0.075403           0.079688               0.079538   
2  0.690212      0.239215           0.239842               0.239758   
3  0.612266      0.380807           0.378665               0.378624   
4  0.387679      0.586044           0.597164               0.596944   
5  0.031459      0.918846           0.918798               0.918784   
6  0.010000      1.000000           1.000000               1.000000   
7  0.731250      0.490716           0.551924               0.550909   

   marketcap  enterprisevalue  pricetobook  pricetotangiblebook  \
0   0.010000         0.010000     0.010000             0.010000   
1   0.209104         0.216192     0.631288             0.643693   
2   0.421639         0.427283     0.918235             0.927890   
3   0.353469         0.350870     0.523418             0.522287   
4   0.738295         0.744178     1.000000             1.000000   
5   1.000000         1.000000     0.983072             0.977509   
6   0.655399         0.634489     0.452019             0.442105   
7   0.448379         0.457856     0.585244             0.582595   

   pricetorevenue  pricetoearnings  dividendyi

In [144]:
period

'QTR'

In [156]:
pca

profitability  solvency  liquidity  valuation  efficiency
0        0.272841 -1.227660   0.923537   1.524462    2.379990
1        0.196993 -1.242430   0.887322   1.524462    2.335094
2       -0.199415 -1.237773   0.900029   1.524462    2.164886
3       -0.423921 -1.060391   1.222818   0.107221    2.122127
4       -0.022394 -1.030181   1.131626   0.149499    2.094391
5       -0.577555 -0.542751   0.660716  -0.388979   -0.562345
6       -0.411415 -0.629046   0.881338  -0.546806   -0.461874
7       -0.471534 -0.939449   1.057174  -0.202818   -0.534417
8        0.129687 -0.851515   0.678359  -0.377896   -0.417938
9        0.334688 -0.629817   0.259589  -0.106691   -0.255086
10      -0.095127 -0.596326   0.567080  -0.096204   -0.359301
11      -0.190664 -0.572432   0.578926  -0.259599   -0.403556
12       1.118524 -0.676048   0.141490  -0.061563   -0.075248
13       2.062050 -0.717743  -0.174328  -0.174020    0.173830
14       0.870625 -0.638984  -0.129973  -0.290265   -0.091603
15       0.125718 -0.562771  -0.190415  -0.360709   -0.307762
16       0.444101 -0.077869  -0.632952  -0.256752   -0.265821
17      -0.218783  0.299783  -0.355830  -0.489973   -0.434979
18      -0.258356 -0.021850  -0.615859  -0.432402   -0.481194
19      -0.896428  0.554328  -0.516288  -0.330052   -0.695597
20      -0.778697  0.459320  -0.714393  -0.164111   -0.758838
21      -0.570315  0.872879  -0.234544  -0.187113   -0.733201
22      -0.616696  0.822173  -0.901671  -0.119670   -0.719291
23      -1.038414  0.836011  -0.759057  -0.147600   -0.890648
24       0.410640  0.975235  -0.991818  -0.006586   -0.454509
25      -0.700913  1.714645  -1.142319   0.005636   -0.839416
26      -0.002347  2.269440  -0.978984  -0.013890   -0.623589
27      -0.054184  2.103722  -0.773562   0.018032   -0.647171
28       1.561292  2.347497  -0.778011   0.159927   -0.256933

In [160]:
ticks = ["CMG","BJRI"]
dict_frames = {} 

for ticker in ticks: 
    for period in ["FY","QTR"]:
        if period == "FY":
            for request in ["calculations", "income_statement", "cash_flow_statement","balance_sheet"]:
                
                original = pd.read_csv("org_"+period+"_"+request+"_"+ticker+".csv")
                normalised = pd.read_csv("sta_"+period+"_"+request+"_"+ticker+".csv")
            
                corr_ft = correlation(True, 10,3,normalised)
                uncorr_ft = correlation(False,-10,3, normalised)
                pca_df = pca_transform(normalised, request)
                for i in ticks:
                    if i not in ticker:
                        bench = pd.read_csv("sta_"+period+"_"+request+"_"+i+".csv")
                        benched_pos_ft, benched_neg_ft, full = bench_comp(normalised, bench, request, period)
                vola_df = normalised[full]
                volatile_ft = volat(True,3,normalised,vola_df)
                stable_ft = volat(False,3,normalised,vola_df)
                smooth_df = smoothed(normalised)
                
                dict_frames[ticker,period,request,"original_df"] = original
                dict_frames[ticker,period,request,"normalised_df"] = normalised
                dict_frames[ticker,period,request,"corr_ft"] = corr_ft
                dict_frames[ticker,period,request,"uncorr_ft"] = uncorr_ft
                dict_frames[ticker,period,request,"pca_df"] = pca_df
                dict_frames[ticker,period,request,"benchmark_df"] = bench
                dict_frames[ticker,period,request,"bench_pos_ft"] = benched_pos_ft
                dict_frames[ticker,period,request,"bench_neg_ft"] = benched_neg_ft
                dict_frames[ticker,period,request,"volatile_ft"] = volatile_ft
                dict_frames[ticker,period,request,"stable_ft"] = stable_ft
                dict_frames[ticker,period,request,"smooth_df"] = smooth_df
                

    
        elif period == "QTR":
              for request in ["calculations"]:
                    
                original = pd.read_csv("org_"+period+"_"+request+"_"+ticker+".csv")
                normalised = pd.read_csv("sta_"+period+"_"+request+"_"+ticker+".csv")
            
                corr_ft = correlation(True, 10,3,normalised)
                uncorr_ft = correlation(False,-10,3, normalised)
                pca_df = pca_transform(normalised, request)
                for i in ticks:
                    if i not in ticker:
                        bench = pd.read_csv("sta_"+period+"_"+request+"_"+i+".csv")
                        benched_pos_ft, benched_neg_ft, full = bench_comp(normalised, bench, request, period)
                vola_df = normalised[full]
                volatile_ft = volat(True,3,normalised,vola_df)
                stable_ft = volat(False,3,normalised,vola_df)
                smooth_df = smoothed(normalised)
                
                dict_frames[ticker,period,request,"original_df"] = original
                dict_frames[ticker,period,request,"normalised_df"] = normalised
                dict_frames[ticker,period,request,"corr_ft"] = corr_ft
                dict_frames[ticker,period,request,"uncorr_ft"] = uncorr_ft
                dict_frames[ticker,period,request,"pca_df"] = pca_df
                dict_frames[ticker,period,request,"benchmark_df"] = bench
                dict_frames[ticker,period,request,"bench_pos_ft"] = benched_pos_ft
                dict_frames[ticker,period,request,"bench_neg_ft"] = benched_neg_ft
                dict_frames[ticker,period,request,"volatile_ft"] = volatile_ft
                dict_frames[ticker,period,request,"stable_ft"] = stable_ft
                dict_frames[ticker,period,request,"smooth_df"] = smooth_df

Index(['Type', 'Dimension'], dtype='object')
[['revenuegrowth' 'profitability']
 ['nopat' 'profitability']
 ['nopatmargin' 'profitability']
 ['investedcapital' 'solvency']
 ['investedcapitalturnover' 'solvency']
 ['investedcapitalincreasedecrease' 'solvency']
 ['freecashflow' 'liquidity']
 ['ebit' 'profitability']
 ['ebitda' 'profitability']
 ['capex' 'solvency']
 ['dfcfnwc' 'liquidity']
 ['dfnwc' 'liquidity']
 ['nwc' 'liquidity']
 ['bookvaluepershare' 'valuation']
 ['tangbookvaluepershare' 'valuation']
 ['pricetobook' 'valuation']
 ['pricetotangiblebook' 'valuation']
 ['pricetorevenue' 'valuation']
 ['pricetoearnings' 'valuation']
 ['dividendyield' 'valuation']
 ['earningsyield' 'profitability']
 ['evtoinvestedcapital' 'solvency']
 ['evtorevenue' 'solvency']
 ['evtoebitda' 'solvency']
 ['evtoebit' 'solvency']
 ['evtonopat' 'solvency']
 ['evtoocf' 'solvency']
 ['evtofcff' 'solvency']
 ['ebitdagrowth' 'profitability']
 ['ebitgrowth' 'profitability']
 ['nopatgrowth' 'profitability']
 ['n

/Users/dereksnow/anaconda/envs/py36/lib/python3.6/site-packages/ipykernel/__main__.py:3: FutureWarning:

pd.rolling_mean is deprecated for DataFrame and will be removed in a future version, replace with 
	DataFrame.rolling(window=8,center=False).mean()

/Users/dereksnow/anaconda/envs/py36/lib/python3.6/site-packages/ipykernel/__main__.py:5: FutureWarning:

pd.rolling_mean is deprecated for DataFrame and will be removed in a future version, replace with 
	DataFrame.rolling(window=8,center=False).mean()



                                   0
weightedavedilutedsharesos  3.749716
netincometocommon           4.703481
netincome                   4.703481
netincomecontinuing         4.703481
otherspecialcharges         4.045697
weightedavebasicsharesos    2.807106
operatingcostofrevenue      6.428365
totalcostofrevenue          6.428365
operatingrevenue            7.038320
totalrevenue                7.038320
                                        0
netincometocommon                4.545804
netincome                        4.545804
netincomecontinuing              4.545804
otherspecialcharges              3.931324
weightedavebasicsharesos         2.819632
operatingcostofrevenue           6.256362
totalcostofrevenue               6.256362
operatingrevenue                 6.843582
totalrevenue                     6.843582
weightedavebasicdilutedsharesos  2.441354
Index(['Type', 'Dimension'], dtype='object')
[['cashincometaxespaid' 'cash-flow']
 ['cashinterestpaid' 'cash-flow']
 ['depreciation

In [162]:
from six.moves import cPickle as pickle #for performance
from __future__ import print_function
import numpy as np

def save_dict(di_, filename_):
    with open(filename_, 'wb') as f:
        pickle.dump(di_, f)

def load_dict(filename_):
    with open(filename_, 'rb') as f:
        ret_di = pickle.load(f)
    return ret_di

save_dict(dict_frames, './data.pkl')
dict_frames = load_dict('./data.pkl')

In [167]:
len(dict_frames)

110

In [145]:
ticks = ["CMG","BJRI"]
dict_frames = {} 
for ticker in ticks: 
    for period in ["FY","QTR"]:
        if period == "FY":
            for request in ["calculations", "income_statement", "cash_flow_statement","balance_sheet"]:
                
                original = pd.read_csv("org_"+period+"_"+request+"_"+ticker+".csv")
                normalised = pd.read_csv("sta_"+period+"_"+request+"_"+ticker+".csv")
                corr = correlation(True, 10,3,normalised)
                corr = normalised[corr].copy()
                corr.to_csv("sta_"+period+"_"+request+"_"+ticker+"corr"+".csv")
                uncorr = correlation(False,-10,3, normalised)
                uncorr = normalised[uncorr].copy()
                uncorr.to_csv("sta_"+period+"_"+request+"_"+ticker+"uncorr"+".csv")
                pca = pca_transform(normalised, request)
                for i in ticks:
                    if i not in ticker:
                        bench = pd.read_csv("sta_"+period+"_"+request+"_"+i+".csv")
                        benched_pos, benched_neg, full = bench_comp(normalised, bench, request, period)
                vola = normalised[full]
                volatile = volat(True,3,normalised,vola)
                stable = volat(False,3,normalised,vola)
                smooth = smoothed(normalised)
                
                dict_frames[ticker,period,request,original] = original
                
                

    
        elif period == "QTR":
              for request in ["calculations"]:
                    
                original = pd.read_csv("org_"+period+"_"+request+"_"+ticker+".csv")
                normalised = pd.read_csv("sta_"+period+"_"+request+"_"+ticker+".csv")
            
                corr = correlation(True, 10,3,normalised)
                corr = normalised[corr].copy()
                
                corr.to_csv("sta_"+period+"_"+request+"_"+ticker+"corr"+".csv")
                uncorr = correlation(False,-10,3, normalised)
                uncorr = normalised[uncorr].copy()
                uncorr.to_csv("sta_"+period+"_"+request+"_"+ticker+"uncorr"+".csv")
                pca = pca_transform(normalised, request)
                pca.to_csv("sta_"+period+"_"+request+"_"+ticker+"pca"+".csv")
                for i in ticks:
                    if i not in ticker:
                        bench = pd.read_csv("sta_"+period+"_"+request+"_"+i+".csv")
                        benched_pos, benched_neg, full = bench_comp(normalised, bench, request, period)
                        normalised[benched_pos].to_csv("sta_"+period+"_"+request+"_"+ticker+"pos_benched_to_"+i+".csv")
                        normalised[benched_neg].to_csv("sta_"+period+"_"+request+"_"+ticker+"pos_benched_to_"+i+".csv")
                vola = normalised[full]
                volatile = volat(True,3,normalised,vola)
                stable = volat(False,3,normalised,vola)
                smooth = smoothed(normalised)

Index(['Type', 'Dimension'], dtype='object')
[['revenuegrowth' 'profitability']
 ['nopat' 'profitability']
 ['nopatmargin' 'profitability']
 ['investedcapital' 'solvency']
 ['investedcapitalturnover' 'solvency']
 ['investedcapitalincreasedecrease' 'solvency']
 ['freecashflow' 'liquidity']
 ['ebit' 'profitability']
 ['ebitda' 'profitability']
 ['capex' 'solvency']
 ['dfcfnwc' 'liquidity']
 ['dfnwc' 'liquidity']
 ['nwc' 'liquidity']
 ['bookvaluepershare' 'valuation']
 ['tangbookvaluepershare' 'valuation']
 ['pricetobook' 'valuation']
 ['pricetotangiblebook' 'valuation']
 ['pricetorevenue' 'valuation']
 ['pricetoearnings' 'valuation']
 ['dividendyield' 'valuation']
 ['earningsyield' 'profitability']
 ['evtoinvestedcapital' 'solvency']
 ['evtorevenue' 'solvency']
 ['evtoebitda' 'solvency']
 ['evtoebit' 'solvency']
 ['evtonopat' 'solvency']
 ['evtoocf' 'solvency']
 ['evtofcff' 'solvency']
 ['ebitdagrowth' 'profitability']
 ['ebitgrowth' 'profitability']
 ['nopatgrowth' 'profitability']
 ['n

/Users/dereksnow/anaconda/envs/py36/lib/python3.6/site-packages/ipykernel/__main__.py:3: FutureWarning:

pd.rolling_mean is deprecated for DataFrame and will be removed in a future version, replace with 
	DataFrame.rolling(window=8,center=False).mean()

/Users/dereksnow/anaconda/envs/py36/lib/python3.6/site-packages/ipykernel/__main__.py:5: FutureWarning:

pd.rolling_mean is deprecated for DataFrame and will be removed in a future version, replace with 
	DataFrame.rolling(window=8,center=False).mean()



Index(['Type', 'Dimension'], dtype='object')
[['cashincometaxespaid' 'cash-flow']
 ['cashinterestpaid' 'cash-flow']
 ['depreciationexpense' 'cash-flow']
 ['increasedecreaseinoperatingcapital' 'cash-flow']
 ['issuanceofdebt' 'cash-flow']
 ['netcashfromcontinuingfinancingactivities' 'cash-flow']
 ['netcashfromcontinuinginvestingactivities' 'cash-flow']
 ['netcashfromcontinuingoperatingactivities' 'cash-flow']
 ['netcashfromfinancingactivities' 'cash-flow']
 ['netcashfrominvestingactivities' 'cash-flow']
 ['netcashfromoperatingactivities' 'cash-flow']
 ['netchangeincash' 'cash-flow']
 ['netincome' 'cash-flow']
 ['netincomecontinuing' 'cash-flow']
 ['noncashadjustmentstonetincome' 'cash-flow']
 ['otherfinancingactivitiesnet' 'cash-flow']
 ['otherinvestingactivitiesnet' 'cash-flow']
 ['purchaseofinvestments' 'cash-flow']
 ['purchaseofplantpropertyandequipment' 'cash-flow']
 ['repaymentofdebt' 'cash-flow']
 ['repurchaseofcommonequity' 'cash-flow']
 ['saleofinvestments' 'cash-flow']
 ['saleof

In [43]:
corr

earningsyield     rnnoa   dfcfnwc
0       1.000000  0.728548  0.929285
1       0.572233  0.591707  1.000000
2       0.420473  0.390262  0.583805
3       0.639651  0.247922  0.578430
4       0.411543  0.227843  0.596578
5       0.434943  0.010000  0.297015
6       0.687947  0.055121  0.439358
7       0.010000  1.000000  0.010000

In [42]:
dis

{'arturnover': 7.222062317191005,
 'compoundleveragefactor': 7.597109101901725,
 'dfcfnwc': 5.938791012807992,
 'earningsyield': 3.018053585295071,
 'finleverage': 7.75823940250987,
 'leverageratio': 7.597109101901725,
 'netdebt': 7.718998178092922,
 'netnonopex': 6.529382840270653,
 'netnonopobligations': 7.718998178092922,
 'rnnoa': 4.9998169698363695}

In [36]:
dar = pd.DataFrame(list(dis.values()), index=list(dis.keys())).sort_values(0).ix[:3].index.values

TypeError: 'numpy.ndarray' object is not callable

In [28]:
pd.DataFrame(list(dis.values()), index=list(dis.keys())).sort_values(0).ix[:10].index.values

array(['earningsyield', 'rnnoa', 'dfcfnwc', 'netnonopex', 'arturnover',
       'leverageratio', 'compoundleveragefactor', 'netnonopobligations',
       'netdebt', 'finleverage'], dtype=object)

In [37]:
    related = pd.DataFrame(list(dis.values()), index=list(dis.keys())).sort_values().ix[:select].index.values



TypeError: 'numpy.ndarray' object is not callable

In [154]:
# -*- coding: utf-8 -*-
import pandas as pd

import dash
from dash import Dash
from dash.dependencies import Input, Output
import dash_core_components as dcc
import dash_html_components as html
import colorlover as cl
import numpy as np
from flask import Flask
#
df_goog = pd.read_csv("goog.csv")

df_goog

def create_figure():
    
    for fundamental in df_goog.drop("year").columns:

        x = df_goog[fundamental]
        y = df_goog["year"]

        hoverinfo = 'text'
        width = 1
        if color == 'lightgrey':
            color = 'grey'
        hoverinfo = 'text'

        label = df_goog.index

        traces.append({
            'x': x,
            'y': y,
            'mode': 'lines',
            'line': {
                'color': color,
                'width': width
            },
            'text': [
                ('<b>{}</b><br>'
                 'Overall job growth: {}%<br>'
                 'Wages: ${} / hour<br>'
                 'Jobs: {}k<br>{}').format(
                    1,
                    2,
                    3,
                    3,
                    5
                )   ],
            
        })


    layout = {
        'xaxis': {
            'showgrid': False,
            'showline': False,
            'zeroline': False,
            'showticklabels': False,
            'ticks': '',
            'title': '← Lower Wages        Industries        Higher Wages →'
        },
        'yaxis': {
            'showgrid': False,
            'showticklabels': False,
            'zeroline': False,
            'ticks': '',
            'title': 'Jobs'
        },
        'showlegend': not bool(highlight_cescode),
        'hovermode': 'closest',
        'legend': {
            'x': 0.8,
            'y': 0.95,
            'xanchor': 'left'
        },
        'annotations': annotations,
        'margin': {'t': 20, 'b': 20, 'r': 0, 'l': 20},
        'font': {'size': 12}
    }

    return {'data': traces, 'layout': layout}

server = Flask(__name__)
app = Dash(__name__, server=server, url_base_pathname='/dash/gallery/recession-report/', csrf_protect=False)
app.css.append_css({
    'external_url': (
        'https://cdn.rawgit.com/chriddyp/0247653a7c52feb4c48437e1c1837f75'
        '/raw/a68333b876edaf62df2efa7bac0e9b3613258851/dash.css'
    )
})

layout = html.Div([


    html.Div(
        dcc.Dropdown(
            options=[
                {'label': c, 'value': c}
                for c in sorted(list(df_goog.columns.unique()))
            ],
            value=['revenuegrowth',"nopat"],
            multi=True,
            id='category-filter',
        ), className='container', style={'maxWidth': '650px'}),
    html.Div(id='filtered-content'),


])


app.layout = layout


@app.callback(
    Output('filtered-content', 'children'),
    [Input('category-filter', 'value')])
def filter(selected_values):
    figure = create_figure(
        list(df_goog[
            df_goog.columns.isin(selected_values)
        ]) if selected_values else None,
        skip_labels=['-'],
    )

    for trace in figure['data']:
        trace['hoverinfo'] = 'text'

    return dcc.Graph(
        id='filtered-graph',
        figure=figure
    )
##


if __name__ == '__main__':
    app.run_server(debug=True, host='127.0.0.1', port=7060, threaded=True)

In [158]:
%tb

SystemExit: 1

In [19]:
df_jobs = pd.read_csv('nyt_255_ces.csv')
df_wages = pd.read_csv('nyt_255_wages.csv')


In [152]:
df_goog

year                                     2007          2008          2009  \
revenuegrowth                    0.000000e+00  3.134880e-01  8.510700e-02   
nopat                            3.766914e+09  4.789589e+09  6.466321e+09   
nopatmargin                      2.270050e-01  2.197460e-01  2.734060e-01   
investedcapital                  0.000000e+00  1.230793e+10  1.139000e+10   
investedcapitalturnover          0.000000e+00  1.770900e+00  1.996000e+00   
investedcapitalincreasedecrease  0.000000e+00  0.000000e+00 -9.179310e+08   
freecashflow                     0.000000e+00  0.000000e+00  7.384252e+09   
netnonopex                      -4.368061e+08  5.625889e+08 -5.367856e+07   
netnonopobligations              0.000000e+00 -1.593093e+10 -2.461400e+10   
ebit                             5.673980e+09  6.948000e+09  8.381000e+09   
depreciationandamortization      9.676580e+08  1.500000e+09  1.524000e+09   
ebitda                           6.641638e+09  8.448000e+09  9.905000e+09   
capex                            2.402840e+09  2.359000e+09  8.100000e+08   
dfcfnwc                          0.000000e+00  2.030321e+09  1.935000e+09   
dfnwc                            0.000000e+00  1.787609e+10  2.642000e+10   
nwc                              0.000000e+00  1.787609e+10  2.642000e+10   
debt                             0.000000e+00  0.000000e+00  0.000000e+00   
ltdebtandcapleases               0.000000e+00  0.000000e+00  0.000000e+00   
netdebt                          0.000000e+00 -1.593093e+10 -2.461400e+10   
totalcapital                     0.000000e+00  2.823886e+10  3.600400e+10   
bookvaluepershare                0.000000e+00  8.891330e+01  1.126886e+02   
tangbookvaluepershare            0.000000e+00  7.053630e+01  9.491710e+01   
marketcap                        2.187151e+11  9.770964e+10  1.980836e+11   
enterprisevalue                  0.000000e+00  8.177871e+10  1.734696e+11   
pricetobook                      0.000000e+00  3.460100e+00  5.501700e+00   
pricetotangiblebook              0.000000e+00  4.361600e+00  6.531800e+00   
pricetorevenue                   1.318040e+01  4.482900e+00  8.375300e+00   
pricetoearnings                  5.202890e+01  2.311560e+01  3.038090e+01   
dividendyield                    0.000000e+00  0.000000e+00  0.000000e+00   
earningsyield                    1.922000e-02  4.326100e-02  3.291500e-02   
...                                       ...           ...           ...   
augmentedpayoutratio             0.000000e+00  0.000000e+00  0.000000e+00   
ocftocapex                       2.403577e+00  3.328953e+00  1.150124e+01   
stdebttocap                      0.000000e+00  0.000000e+00  0.000000e+00   
ltdebttocap                      0.000000e+00  0.000000e+00  0.000000e+00   
debttototalcapital               0.000000e+00  0.000000e+00  0.000000e+00   
preferredtocap                   0.000000e+00  0.000000e+00  0.000000e+00   
noncontrolinttocap               0.000000e+00  0.000000e+00  0.000000e+00   
commontocap                      0.000000e+00  1.000000e+00  1.000000e+00   
debttoebitda                     0.000000e+00  0.000000e+00  0.000000e+00   
netdebttoebitda                  0.000000e+00  0.000000e+00  0.000000e+00   
ltdebttoebitda                   0.000000e+00  0.000000e+00  0.000000e+00   
debttonopat                      0.000000e+00  0.000000e+00  0.000000e+00   
netdebttonopat                   0.000000e+00  0.000000e+00  0.000000e+00   
ltdebttonopat                    0.000000e+00  0.000000e+00  0.000000e+00   
altmanzscore                     0.000000e+00  1.929470e+01  2.919640e+01   
ebittointerestex                 0.000000e+00  0.000000e+00  0.000000e+00   
nopattointerestex                0.000000e+00  0.000000e+00  0.000000e+00   
ebitlesscapextointerestex        0.000000e+00  0.000000e+00  0.000000e+00   
nopatlesscapextointex            0.000000e+00  0.000000e+00  0.000000e+00   
ocftointerestex                  0.000000e+00  0.000000e+00  0.000000e+00

In [141]:
df_goog["index"]

0                        revenuegrowth
1                                nopat
2                          nopatmargin
3                      investedcapital
4              investedcapitalturnover
5      investedcapitalincreasedecrease
6                         freecashflow
7                           netnonopex
8                  netnonopobligations
9                                 ebit
10         depreciationandamortization
11                              ebitda
12                               capex
13                             dfcfnwc
14                               dfnwc
15                                 nwc
16                                debt
17                  ltdebtandcapleases
18                             netdebt
19                        totalcapital
20                   bookvaluepershare
21               tangbookvaluepershare
22                           marketcap
23                     enterprisevalue
24                         pricetobook
25                 pricet

In [142]:
df_goog = pd.read_csv("goog.csv")

df_goog.set_index("year",drop=True,inplace=True)

df_goog = df_goog.T

In [147]:
df_goog.index.isin(["revenuegrowth"])

array([ True, False, False, False, False, False, False, False, False,
       False, False, False, False, False, False, False, False, False,
       False, False, False, False, False, False, False, False, False,
       False, False, False, False, False, False, False, False, False,
       False, False, False, False, False, False, False, False, False,
       False, False, False, False, False, False, False, False, False,
       False, False, False, False, False, False, False, False, False,
       False, False, False, False, False, False, False, False, False,
       False, False, False, False, False, False, False, False, False,
       False, False, False, False, False, False, False, False, False,
       False, False, False, False, False, False, False, False, False,
       False, False, False, False, False, False, False, False, False,
       False, False, False, False, False, False, False, False, False,
       False, False, False, False], dtype=bool)

In [149]:
traces[-1]['x'][-1]

2007.2

In [151]:
traces[-1]['y'].iloc[-1]

-4.4269335398560887

In [64]:
series = {
    'absolute_wages': {},
    'absolute_jobs': {},
    'relative_job': {},
    'relative_wages': {},
    'meta': {},
    'job_growth': {}
}
for i in range(len(df_goog)-1):
    i = i +1
    jobs_meta = df_goog.ix[:,1:].iloc[i, 0]
    name = jobs_meta
    jobs_row = df_goog.ix[:,1:].iloc[i, 0:]

    wages_row = pd.Series(df_goog.columns[1:].values, index=df_goog.columns[1:].values) 
    
        # Collect data
    series['absolute_wages'] = wages_row
    series['absolute_jobs'] = jobs_row
    series['relative_job'] = jobs_row
    series['relative_wages'] = wages_row
    series['meta'] = jobs_meta
    series['job_growth'] = jobs_row


highlight_cescode=None
skip_labels=[] 
show_only=[]

max_wage = 2007
min_wage = 2016
# Construct the charts
scale = cl.scales['5']['div']['RdBu']
traces = []
annotations = []
for cescode in series['absolute_wages'].keys():
    growth = series['relative_job']
    # Construct initial chart

    # x's initial position is the initial wage
    # and its width is constant to signifiy time
    initial_wage = series['absolute_wages'].iloc[0]
    relative_wage = max_wage
    x = np.linspace(
        relative_wage,
        relative_wage + 0.2,
        len(series['absolute_wages'])
    )

    # convert growth over time to a relative scale and
    # jobs created across all industries to relative scale
    relative_growth_across_time = ((series['absolute_jobs'] -
                      series['absolute_jobs'].iloc[0]) /
                      series['absolute_jobs'].iloc[-1])

    max_jobs_created = 1
    min_jobs_created = 2
    jobs = series['absolute_jobs']
    relative_growth_across_industry = ((jobs.iloc[-1] - jobs.iloc[0]) - min_jobs_created) / max_jobs_created
    y = relative_growth_across_time + (relative_growth_across_industry * 2)
    growth = 12

    if growth > 20:
        color = scale[4]
        legendgroup = '>20%'
        name = 'Greater than 20%'
    elif growth > 10:
        color = scale[3]
        legendgroup = '>10%'
        name = 'Between 10% and 20%'
    elif growth > -10:
        color = 'lightgrey'
        legendgroup = '>-10%'
        name = 'Between -10% and 10%'
    elif growth > -20:
        color = scale[1]
        legendgroup = '>-20%'
        name = 'Between -20% and -10%'
    else:
        color = scale[0]
        legendgroup = '<-20%'
        name = 'Less than -20%'

    if highlight_cescode and cescode not in highlight_cescode:
        color = 'lightgrey'

    hoverinfo = 'text'
    width = 1
    if highlight_cescode and cescode in highlight_cescode:
        width = 2.5
        if color == 'lightgrey':
            color = 'grey'
        hoverinfo = 'text'
    elif highlight_cescode:
        width = 0.5
        hoverinfo = 'none'

    label = jobs_meta

    traces.append({
        'x': x,
        'y': y,
        'mode': 'lines',
        'line': {
            'color': color,
            'width': width
        },
        'text': [
            ('<b>{}</b><br>'
             'Overall job growth: {}%<br>'
             'Wages: ${} / hour<br>'
             'Jobs: {}k<br>{}').format(
                label,
                np.around(growth, decimals=1),
                np.around(wage_in_year, decimals=1),
                jobs_in_year,
                year
            )
            for year, jobs_in_year, wage_in_year in zip(
                list(jobs.index),
                list(jobs),
                list(series['absolute_wages'])
            )
        ],
        'legendgroup': legendgroup,
        'name': name,
        'hoverinfo': hoverinfo,
        'showlegend': (
            False if legendgroup in [t['legendgroup'] for t in traces]
            else True
        )
    })

    if (highlight_cescode and cescode in highlight_cescode and
            (skip_labels and label not in skip_labels) or
            (show_only and label in show_only)):
        annotations.append({
            'x': traces[-1]['x'][-1], 'xref': 'x', 'xanchor': 'left',
            'y': traces[-1]['y'][-1], 'yref': 'y', 'yanchor': 'top',
            'showarrow': False,
            'text': label,
            'font': {'size': 12},
            'bgcolor': 'rgba(255, 255, 255, 0.5)'
        })

# reorder traces to reorder legend items
highlight_cescode = True
if not highlight_cescode:
    def get_trace_index(traces, legendgroup):
        for i, trace in enumerate(traces):
            if trace['showlegend'] and trace['legendgroup'] == legendgroup:
                return i
    traces.insert(0, traces.pop(get_trace_index(traces, '<-20%')))
    traces.insert(0, traces.pop(get_trace_index(traces, '>-20%')))
    traces.insert(0, traces.pop(get_trace_index(traces, '>-10%')))
    traces.insert(0, traces.pop(get_trace_index(traces, '>10%')))
    traces.insert(0, traces.pop(get_trace_index(traces, '>20%')))
else:
    # move highlighted traces to the end
    for i, trace in enumerate(traces):
        if trace['line']['width'] != 2.5:
            traces.insert(0, traces.pop(i))


if not highlight_cescode:
    annotations = [{
        'x': 0.8, 'xref': 'paper', 'xanchor': 'left',
        'y': 0.95, 'yref': 'paper', 'yanchor': 'bottom',
        'text': '<b>Job Growth</b>',
        'showarrow': False
    }]

layout = {
    'xaxis': {
        'showgrid': False,
        'showline': False,
        'zeroline': False,
        'showticklabels': False,
        'ticks': '',
        'title': '← Lower Wages        Industries        Higher Wages →'
    },
    'yaxis': {
        'showgrid': False,
        'showticklabels': False,
        'zeroline': False,
        'ticks': '',
        'title': 'Jobs'
    },
    'showlegend': not bool(highlight_cescode),
    'hovermode': 'closest',
    'legend': {
        'x': 0.8,
        'y': 0.95,
        'xanchor': 'left'
    },
    'annotations': annotations,
    'margin': {'t': 20, 'b': 20, 'r': 0, 'l': 20},
    'font': {'size': 12}
}

In [138]:
traces

[{'hoverinfo': 'text',
  'legendgroup': '>10%',
  'line': {'color': 'rgb(146,197,222)', 'width': 1},
  'mode': 'lines',
  'name': 'Between 10% and 20%',
  'showlegend': False,
  'text': ['<b>0.34193</b><br>Overall job growth: 12%<br>Wages: $2007 / hour<br>Jobs: 0.34193k<br>2007',
   '<b>0.34193</b><br>Overall job growth: 12%<br>Wages: $2008 / hour<br>Jobs: 0.268536k<br>2008',
   '<b>0.34193</b><br>Overall job growth: 12%<br>Wages: $2009 / hour<br>Jobs: 0.35436100000000004k<br>2009',
   '<b>0.34193</b><br>Overall job growth: 12%<br>Wages: $2010 / hour<br>Jobs: 0.3682k<br>2010',
   '<b>0.34193</b><br>Overall job growth: 12%<br>Wages: $2011 / hour<br>Jobs: 0.325181k<br>2011',
   '<b>0.34193</b><br>Overall job growth: 12%<br>Wages: $2012 / hour<br>Jobs: 0.314277k<br>2012',
   '<b>0.34193</b><br>Overall job growth: 12%<br>Wages: $2013 / hour<br>Jobs: 0.28636999999999996k<br>2013',
   '<b>0.34193</b><br>Overall job growth: 12%<br>Wages: $2014 / hour<br>Jobs: 0.261496k<br>2014',
   '<b>0.3419

In [116]:
series['absolute_jobs']

year
index    pretaxincomemargin
2007                0.34193
2008               0.268536
2009               0.354361
2010                 0.3682
2011               0.325181
2012               0.314277
2013                0.28637
2014               0.261496
2015               0.262052
2016               0.267525
Name: 120, dtype: object

In [139]:
layout

{'annotations': [],
 'font': {'size': 12},
 'hovermode': 'closest',
 'legend': {'x': 0.8, 'xanchor': 'left', 'y': 0.95},
 'margin': {'b': 20, 'l': 20, 'r': 0, 't': 20},
 'showlegend': False,
 'xaxis': {'showgrid': False,
  'showline': False,
  'showticklabels': False,
  'ticks': '',
  'title': '← Lower Wages        Industries        Higher Wages →',
  'zeroline': False},
 'yaxis': {'showgrid': False,
  'showticklabels': False,
  'ticks': '',
  'title': 'Jobs',
  'zeroline': False}}

In [59]:
traces

[{'hoverinfo': 'text',
  'legendgroup': '>20%',
  'line': {'color': 'rgb(5,113,176)', 'width': 1},
  'mode': 'lines',
  'name': 'Greater than 20%',
  'showlegend': True,
  'text': ['<b>Oil and gas extraction</b><br>Overall job growth: 42.7%<br>Wages: $28.8 / hour<br>Jobs: 119.8k<br>2004-01-01',
   '<b>Oil and gas extraction</b><br>Overall job growth: 42.7%<br>Wages: $29.0 / hour<br>Jobs: 121.2k<br>2004-02-01',
   '<b>Oil and gas extraction</b><br>Overall job growth: 42.7%<br>Wages: $29.4 / hour<br>Jobs: 121.4k<br>2004-03-01',
   '<b>Oil and gas extraction</b><br>Overall job growth: 42.7%<br>Wages: $29.3 / hour<br>Jobs: 122.9k<br>2004-04-01',
   '<b>Oil and gas extraction</b><br>Overall job growth: 42.7%<br>Wages: $29.6 / hour<br>Jobs: 124.2k<br>2004-05-01',
   '<b>Oil and gas extraction</b><br>Overall job growth: 42.7%<br>Wages: $29.7 / hour<br>Jobs: 123.6k<br>2004-06-01',
   '<b>Oil and gas extraction</b><br>Overall job growth: 42.7%<br>Wages: $30.0 / hour<br>Jobs: 123.5k<br>2004-07-0

In [1]:
import intrinio
intrinio.client.username = 'cae7d0c54c6e7fd5363fc315b7fc7a4a'
intrinio.client.password = 'c949ffd2ddebb5e554c151f58db4ee9e'

In [2]:
intrinio.companies('GOOG')

business_address business_phone_no  \
0  1600 AMPHITHEATRE PARKWAY, MOUNTAIN VIEW, CA 9...      650-253-0000   

                ceo         cik company_url  employees entity_legal_form  \
0  Lawrence E. Page  0001652044     abc.xyz      72053              None   

  entity_status hq_address1 hq_address2  ...    \
0          None        None        None  ...     

                                     mailing_address          name  \
0  1600 AMPHITHEATRE PARKWAY, MOUNTAIN VIEW, CA 9...  Alphabet Inc   

       sector                                         securities  \
0  Technology  [{'ticker': 'GOOGL', 'figi_ticker': 'GOOGL:UW'...   

                                   short_description   sic  \
0  Alphabet, Inc. is a holding company, which eng...  7370   

  standardized_active stock_exchange    template ticker  
0                True       NasdaqGS  industrial  GOOGL  

[1 rows x 32 columns]

In [19]:
import intrinio
intrinio.get('companies', identifier='GOOG')

business_address business_phone_no  \
0  1600 AMPHITHEATRE PARKWAY, MOUNTAIN VIEW, CA 9...      650-253-0000   

                ceo         cik company_url  employees entity_legal_form  \
0  Lawrence E. Page  0001652044     abc.xyz      72053              None   

  entity_status hq_address1 hq_address2 hq_address_city  \
0          None        None        None            None   

  hq_address_postal_code                hq_country    hq_state  \
0                   None  United States of America  California   

                inc_country inc_state industry_category  \
0  United States of America  Delaware          Internet   

                   industry_group latest_filing_date     legal_name   lei  \
0  Internet Information Providers         2017-10-27  Alphabet Inc.  None   

                                    long_description  \
0  Alphabet Inc., through its subsidiaries, provi...   

                                     mailing_address          name  \
0  1600 AMPHITHEATRE PARKWAY, MOUNTAIN VIEW, CA 9...  Alphabet Inc   

       sector                                         securities  \
0  Technology  [{'ticker': 'GOOGL', 'figi_ticker': 'GOOGL:UW'...   

                                   short_description   sic  \
0  Alphabet, Inc. is a holding company, which eng...  7370   

  standardized_active stock_exchange    template ticker  
0                True       NasdaqGS  industrial  GOOGL

In [20]:
DARS = intrinio.financials("GOOG", type='FY', statement='calculations')

HTTPError: 429 Client Error: Too Many Requests for url: https://api.intrinio.com/fundamentals/standardized?identifier=GOOG&statement=calculations&type=FY&page_number=1&page_size=250

In [63]:
DARS.to_csv("goog.csv")

In [166]:
DARS

revenuegrowth         nopat  nopatmargin  investedcapital  \
year                                                              
2007       0.000000  3.766914e+09     0.227005     0.000000e+00   
2008       0.313488  4.789589e+09     0.219746     1.230793e+10   
2009       0.085107  6.466321e+09     0.273406     1.139000e+10   
2010       0.239736  8.178066e+09     0.278915     1.581900e+10   
2011       0.292759  9.275666e+09     0.244708     1.819500e+10   
2012       0.214589  1.104597e+10     0.239926     2.866800e+10   
2013       0.205912  1.274945e+10     0.229641     3.313500e+10   
2014       0.188800  1.301788e+10     0.197238     4.352600e+10   
2015       0.136180  1.610591e+10     0.214777     4.928000e+10   
2016       0.203803  1.912796e+10     0.211893     5.076000e+10   

      investedcapitalturnover  investedcapitalincreasedecrease  freecashflow  \
year                                                                           
2007                   0.0000                     0.000000e+00  0.000000e+00   
2008                   1.7709                     0.000000e+00  0.000000e+00   
2009                   1.9960                    -9.179310e+08  7.384252e+09   
2010                   2.1552                     4.429000e+09  3.749066e+09   
2011                   2.2288                     2.376000e+09  6.899666e+09   
2012                   1.9648                     1.047300e+10  5.729743e+08   
2013                   1.7966                     4.467000e+09  8.282448e+09   
2014                   1.7219                     1.039100e+10  2.626876e+09   
2015                   1.6160                     5.754000e+09  1.035191e+10   
2016                   1.8047                     1.480000e+09  1.764796e+10   

        netnonopex  netnonopobligations          ebit  \
year                                                    
2007 -4.368061e+08         0.000000e+00  5.673980e+09   
2008  5.625889e+08        -1.593093e+10  6.948000e+09   
2009 -5.367856e+07        -2.461400e+10  8.381000e+09   
2010 -3.269336e+08        -3.042200e+10  1.079600e+10   
2011 -4.613344e+08        -3.995000e+10  1.232600e+10   
2012  3.089743e+08        -4.304700e+10  1.446900e+10   
2013  1.644839e+07        -5.417400e+10  1.589900e+10   
2014 -1.118124e+09        -6.033400e+10  1.725900e+10   
2015 -2.420878e+08        -7.105100e+10  1.965100e+10   
2016 -3.500394e+08        -8.827600e+10  2.415000e+10   

      depreciationandamortization        ebitda         capex       dfcfnwc  \
year                                                                          
2007                 9.676580e+08  6.641638e+09  2.402840e+09  0.000000e+00   
2008                 1.500000e+09  8.448000e+09  2.359000e+09  2.030321e+09   
2009                 1.524000e+09  9.905000e+09  8.100000e+08  1.935000e+09   
2010                 1.396000e+09  1.219200e+10  4.018000e+09  1.667000e+09   
2011                 1.851000e+09  1.417700e+10  3.438000e+09  1.699000e+09   
2012                 2.962000e+09  1.743100e+10  3.273000e+09  1.551000e+09   
2013                 1.158000e+09  1.705700e+10  7.358000e+09  2.544000e+09   
2014                 0.000000e+00  1.725900e+10  1.095900e+10  1.394000e+09   
2015                 0.000000e+00  1.965100e+10  9.915000e+09  2.941000e+09   
2016                 6.144000e+09  3.029400e+10  9.972000e+09  2.319000e+09   

             dfnwc           nwc          debt  ltdebtandcapleases  \
year                                                                 
2007  0.000000e+00  0.000000e+00  0.000000e+00        0.000000e+00   
2008  1.787609e+10  1.787609e+10  0.000000e+00        0.000000e+00   
2009  2.642000e+10  2.642000e+10  0.000000e+00        0.000000e+00   
2010  3.739200e+10  3.156600e+10  5.826000e+09        0.000000e+00   
2011  4.707000e+10  4.384500e+10  6.211000e+09        2.986000e+09   
2012  5.033900e+10  4.611700e+10  7.210000e+09        2.988000e+09   
2013  6.136100e+10  5.697800e+10  6.619000e+09

In [167]:
from sklearn.preprocessing import MinMaxScaler
from sklearn.preprocessing import StandardScaler

def Standardisation(df):
    listed = list(df)
    scaler = StandardScaler()
    scaled = scaler.fit_transform(df)
    df = pd.DataFrame(scaled)
    df.columns = listed
    return df

def Normalisation(df):
    listed = list(df)
    index = df.index
    scaler = MinMaxScaler()
    scaled = scaler.fit_transform(df)
    df = pd.DataFrame(scaled)
    df.columns = listed
    df.index = index
    return df


In [168]:
DARS = intrinio.financials("GOOG", type='FY', statement='calculations')
DARS.fillna(value=0.00001, inplace=True)
DARS_N = Normalisation(DARS)
DARS_N.to_csv("goog.csv")
goog_df = DARS_N

In [169]:
DARS_N.to_csv("goog.csv")

In [21]:
DARS
DARS.fillna(value=0, inplace=True)

In [4]:
intrinio.companies(query='Restaurant')

cik latest_filing_date                   lei  \
0   0000779544         2017-08-11                  None   
1   0000949373         2014-10-31                  None   
2   0001394156         2017-11-03  549300P5J6ZPY9UO2A26   
3   0001495479         2017-11-02                  None   
4   0001013488         2017-11-06                  None   
5   0000926295         2006-12-05                  None   
6   0001009244         2010-11-17                  None   
7   0000738274               None                  None   
8   0001499934               None                  None   
9   0001342108         2009-06-19                  None   
10  0001526020               None                  None   
11  0001415301         2017-10-13                  None   
12  0000940944         2017-10-03  CY1NFSCCB5GUXC7WZC70   
13  0001534992         2017-11-06                  None   
14  0000039047         2015-08-14                  None   
15  0000825324         2017-08-11                  None   
16  0001617977         2017-11-02  549300JJYD5I17WUYL21   
17  0000817900               None                  None   
18  0001526796         2017-05-16  EV38LH524CKTF1R3C636   
19  0000874691         2012-05-11                  None   
20  0001497074         2015-08-20                  None   
21  0001618756         2017-10-26                  None   
22  0001340995         2008-11-25                  None   
23  0000718332         2017-11-08                  None   
24  0001445918         2016-11-14                  None   
25  0001043505               None                  None   
26  0001585583         2017-10-20                  None   
27  0000809248         2017-11-09                  None   
28  0001369233         2011-11-16                  None   
29  0000749153         2015-11-12                  None   
30  0000786360         2015-11-12                  None   
31  0000908652         2011-03-16                  None   
32  0000879554         2006-05-08                  None   
33  0000919628         2012-12-12                  None   

                                              name ticker  
0                             Ark Restaurants Corp   ARKR  
1               EINSTEIN NOAH RESTAURANT GROUP INC   BAGL  
2              Diversified Restaurant Holdings Inc   BAGR  
3                  Bravo Brio Restaurant Group Inc   BBRG  
4                             BJ's Restaurants Inc   BJRI  
5                 BOSTON RESTAURANT ASSOCIATES INC   BRAI  
6                          MEXICAN RESTAURANTS INC   CASA  
7                 CALIFORNIA BEACH RESTAURANTS INC   CBHR  
8   Country Style Cooking Restaurant Chain Co Ltd    CCSC  
9      CUSTOM RESTAURANT & HOSPITALITY GROUP, INC.   CRHY  
10              CORPORATE RESTAURANT CONCEPTS INC.   CRSQ  
11               Del Frisco's Restaurant Group Inc   DFRG  
12                          Darden Restaurants Inc    DRI  
13                     Fiesta Restaurant Group Inc   FRGI  
14                       Frisch's Restaurants Inc     FRS  
15                      Good Times Restaurants Inc   GTIM  
16                           Habit Restaurants Inc   HABT  
17                 American Restaurant Partners LP  ICTPU  
18                     Ignite Restaurant Group Inc    IRG  
19                    OSI RESTAURANT PARTNERS, LLC    OSI  
20                 Preferred Restaurant Brands Inc   PRBI  
21             Restaurant Brands International Inc    QSR  
22           Restaurant Acquisition Partners, Inc.   RAQP  
23                       Rave Restaurant Group Inc   RAVE  
24          Southern Concepts Restaurant Group Inc   RIBS  
25             Diversified Restaurant Holdings Inc   SAUC  
26                        Del Taco Restaurants Inc   TACO  
27                    Carrols Restaurant Group Inc   TAST  
28                    UFood Restaurant Group, Inc.  UFFCQ  
29               DEL TACO RESTAURANT PROPERTIES II  XXNCB  
30              DEL TACO RESTAURANT PROPERTIES III  XXNCC  
31                       

In [30]:
input.df_final.head()

Unnamed: 0       close        date
0           0  100.000000  2012-01-03
1           1  100.361540  2012-01-04
2           2  100.598543  2012-01-05
3           3  100.583246  2012-01-06
4           4  100.249752  2012-01-09

In [31]:
input.df_final_one.head()

Unnamed: 0       close       date
0           0  100.000000 2012-01-03
1           1  102.191813 2012-01-04
2           2  102.698743 2012-01-05
3           3  102.250418 2012-01-06
4           4   99.551675 2012-01-09

In [29]:

from datetime import datetime, timedelta
import pandas as pd
import inflect
import input


loca = "Jacksonville"
bench = "Chipotle"
print("Chipotle")

loc_frs_dict = {"Jacksonville": input.df_tick, "Wisconsin": input.df_tick, "Michigan" "Jacksonville": input.df_tick}
ben_frs_dict = {"MENU ETF": input.df_final, "Filtered ETF": input.df_final_filt, "Chipotle": input.df_final_one}

df_tick = loc_frs_dict[loca]
df_final = ben_frs_dict[bench]

date_old_str = df_final["date"].head(1).values[0]

df_final["date"] = pd.to_datetime(df_final["date"], format="%Y-%m-%d")
df_tick["date"] = pd.to_datetime(df_tick["date"], format="%Y-%m-%d")

s = date_old_str
days = datetime.now() - datetime(year=int(s[0:4]), month=int(s[5:7]), day=int(s[8:10]))

years_i = round(days.days / 365)


p = inflect.engine()
years_s = p.number_to_words(years_i)

tick = "BJRI"
company = "BJ's"
bench = "MENU ETF"

close_comp = comp_df["close"].tail(1).values[0]
open_comp = comp_df["close"].head(1).values[0]
cagr_comp = ((close_comp / open_comp) ** (1 / (days.days / 365)) - 1) * 100

close_tick = df_tick["close"].tail(1).values[0]
open_tick = df_tick["close"].head(1).values[0]
cagr_tick = ((close_tick / open_tick) ** (1 / (days.days / 365)) - 1) * 100

now = datetime.now()


def past_ret(days):
    tick_df = pd.read_csv("tick_df.csv")
    comp_df = pd.read_csv("comp_df.csv")

    last_year = now - timedelta(days=days)

    # last_year.strftime("%Y-%m-%d")

    tick_df["date"] = pd.to_datetime(tick_df["date"], format="%Y-%m-%d")

    diff = (tick_df.date - last_year)

    indexmax = (diff[(diff < pd.to_timedelta(0))].idxmax())

    last_year_price_tick = tick_df["close"].ix[[indexmax]].values[0]

    ret_y_tick = ((close_tick - last_year_price_tick) / last_year_price_tick) * 100

    comp_df["date"] = pd.to_datetime(comp_df["date"], format="%Y-%m-%d")

    last_year_price_comp = comp_df["close"].ix[[indexmax]].values[0]

    ret_y_comp = ((close_comp - last_year_price_comp) / last_year_price_comp) * 100

    return ret_y_tick, ret_y_comp, last_year_price_tick, last_year_price_comp


ret_y_tick, ret_y_comp, last_year_price_tick, last_year_price_comp = past_ret(365)

_, _, last_m_price_tick, last_m_price_comp = past_ret(30)

### Month
m_ret_tick = (close_tick - last_m_price_tick) / last_m_price_tick
m_ret_comp = (close_comp - last_m_price_comp) / last_m_price_comp

m_ret_tick - m_ret_comp

_, _, last_q_price_tick, last_q_price_comp = past_ret(90)

### Qtr
q_ret_tick = (close_tick - last_q_price_tick) / last_q_price_tick
q_ret_comp = (close_comp - last_q_price_comp) / last_q_price_comp

q_ret_tick - q_ret_comp

line = {}
line[0] = "In the last " + years_s + " years the compounded annual return for " + company + " (" + tick + ") " + "is "
line[1] = "negative " if cagr_tick < 0 else "positive"
line[2] = str(round(abs(cagr_tick), 2)) + "%, compared against the "

line[3.1] = str(round(cagr_comp, 2)) + "% "
line[3.5] = "negative " if cagr_comp < 0 else "positive "
line[4.15] = "return of the benchmark (" + bench + "). "
line[5] = company + " year on year return is "
line[6] = "negative " if ret_y_tick < 0 else "positive"
line[7] = str(round(abs(ret_y_tick), 2)) + "% against the benchmark's "
line[8] = "negative " if ret_y_comp < 0 else "positive "
line[9] = "return of " + str(round(ret_y_comp, 2)) + "%. "

if (ret_y_comp < 0) & ((cagr_tick - cagr_comp) > (ret_y_tick - ret_y_comp)):
    line[10] = company + " year on year performance has however"
    line[11] = " worsened as measured against the relative historical benchmark."

if (ret_y_comp < 0) & ((cagr_tick - cagr_comp) < (ret_y_tick - ret_y_comp)):
    line[10] = company + " year on year performance has also"
    line[11] = " improved as measured against the relative historical benchmark."

if (ret_y_comp > 0) & ((cagr_tick - cagr_comp) > (ret_y_tick - ret_y_comp)):
    line[10] = company + " year on year performance has also"
    line[11] = " worsened as measured against the relative historical benchmark."

if (ret_y_comp > 0) & ((cagr_tick - cagr_comp) < (ret_y_tick - ret_y_comp)):
    line[10] = company + " year on year performance has however"
    line[11] = " improved as measured against the relative historical benchmark."

# Loop the words instead of all the text, faster more efficient

line[13] = " In more recent times " + company + " has"
line[14] = " underperformed " if q_ret_tick - q_ret_comp < 0  else " outperformed "
line[14.5] = "the benchmark on a quarter to quarter basis. "

if (q_ret_tick - q_ret_comp < 0) & (m_ret_tick - m_ret_comp < 0):
    line[14.6] = company + " has also"
    line[14.7] = " underperformed the benchmark in the last month."

if (q_ret_tick - q_ret_comp > 0) & (m_ret_tick - m_ret_comp > 0):
    line[14.6] = company + " has also"
    line[14.7] = " outperformed the benchmark in the last month."

if (q_ret_tick - q_ret_comp < 0) & (m_ret_tick - m_ret_comp > 0):
    line[14.6] = "However, " + company + " has"
    line[14.7] = " outperformed the benchmark in the last month."

if (q_ret_tick - q_ret_comp < 0) & (m_ret_tick - m_ret_comp < 0):
    line[14.6] = "However, " + company + " has"
    line[14.7] = " underperformed the benchmark in the last month."

line[14.8] = "With a monthly return of " + str(round(m_ret_tick*100,2)) + "% against the " + str(round(m_ret_comp*100,2)) + "% of the benchmark."


final_text = ""
for i in line.values():
    final_text = final_text + i
print(final_text)




Chipotle
In the last six years the compounded annual return for BJ's (BJRI) is negative 4.2%, compared against the 13.69% positive return of the benchmark (MENU ETF). BJ's year on year return is negative 11.17% against the benchmark's positive return of 2.82%. BJ's year on year performance has however improved as measured against the relative historical benchmark. In more recent times BJ's has outperformed the benchmark on a quarter to quarter basis. BJ's has also outperformed the benchmark in the last month.With a monthly return of 7.21% against the -1.76% of the benchmark.


In [28]:
import pandas as pd

import datetime

s = [ (int(str(datetime.datetime.now().year)[-2:])-4)+i for i in range(5)]


s_metrics_df = pd.DataFrame([["Type","E","C","S","A","IA"],
                             ["Rating",1,1,1,1,1],
                             ["Sentiment",1,1,1,1,1], 
                             ["Knowledge",1,1,1,1,1],
                             ["Loyalty",1,1,1,1,1]])

c_metrics_df = pd.DataFrame([["Year",s[0],s[1],s[2],s[3],s[4]],
                             ["Solvency",1,1,1,1,1],
                             ["Efficiency",1,1,1,1,1], 
                             ["Profitability",1,1,1,1,1],
                             ["Liquidity",1,1,1,1,1]])


In [27]:
print(c_metrics_df)

               0   1   2   3   4   5
0           Type  13  14  15  16  17
1       Solvency   1   1   1   1   1
2     Efficiency   1   1   1   1   1
3  Profitability   1   1   1   1   1
4      Liquidity   1   1   1   1   1


In [24]:
start

[13, 14, 15, 16, 17]